# Capstone Project - The Battle of the Neighborhoods

## Introduction: Business Problem

In this project we will try to find an optimal location for an Italian restaurant in Toronto. Specifically, this report will be targeted to stakeholders interested in opening an Italian restaurant in Toronto, Canada.

Since there are lots of restaurants in Toronto, we will try to detect locations that are not already crowded with restaurants. We are also particularly interested in areas with no Italian restaurants in vicinity. we would also prefer locations as close to Downtown Toronto as possible, assuming that first two conditions are met. Furthermore, we would like to have the restaurant as close as possible to the neighborhoods whose residents live Italian food. 

We will use our data science powers to generate a few most promissing neighborhoods based on these criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data

Based on definition of our problem, factors that will influence our decission are:

- number of existing restaurants in the neighborhood (any type of restaurant)
- number of and distance to Italian restaurants in the neighborhood, if any
- distance of neighborhood from city center

We decided to scrape the Wikipedia page that lists all the neighborhoods in Toronto and transform the data into a pandas dataframe. 

Following data sources will be needed to extract/generate the required information:

- geographical coordinates of the neighborhoods using the **CSV file provided by IBM**
- coordinate of Toronto will be obtained using **Foursquare API**
- number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd  # library for data analsysis

import json # library to handle JSON files
from pandas.io.json import json_normalize# tranform JSON file into a pandas dataframe
from sklearn.cluster import KMeans# import k-means from clustering stage

# Matplotlib and associated plotting modules
import matplotlib as mpl
import matplotlib.pylab as plt
import matplotlib.cm as cm
import matplotlib.colors as colors


from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library
from folium import plugins
from folium.plugins import HeatMap

import requests

%matplotlib inline

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    altair-3.1.0               |           py36_0         724 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    branca-0.3.1               |             py_0          25 KB  conda-forge
    ca-certificates-2019.6.16  |       hecc5488_0         145 KB  conda-forge
    certifi-2019.6.16          |           py36_1         149 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.2 MB

The following NEW packages will be 

## Neighborhoods

Scrape the Wikipedia page and transform the data into a pandas dataframe

Use pandas to read the table into a pandas dataframe

In [2]:
path = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'

In [3]:
df = pd.read_html(path,attrs = {'class': 'wikitable'})

In [4]:
neighborhoods = pd.DataFrame(df[0])
neighborhoods.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

Drop rows with a borough that is Not assigned

In [5]:
neighborhoods = neighborhoods[neighborhoods.Borough != 'Not assigned']
neighborhoods.head()

Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M5A  Downtown Toronto       Regent Park
6      M6A        North York  Lawrence Heights

Reset the index

In [6]:
neighborhoods = neighborhoods.reset_index(drop = True)
neighborhoods.head()

Postcode           Borough     Neighbourhood
0      M3A        North York         Parkwoods
1      M4A        North York  Victoria Village
2      M5A  Downtown Toronto      Harbourfront
3      M5A  Downtown Toronto       Regent Park
4      M6A        North York  Lawrence Heights

Find cells that have a borough but a Not assigned neighborhood, and set the neighborhood the same as the borough

In [7]:
index_Not_assigned = neighborhoods[neighborhoods['Neighbourhood'] == 'Not assigned'].index
index_Not_assigned

Int64Index([6], dtype='int64')

In [8]:
neighborhoods['Neighbourhood'].replace('Not assigned',neighborhoods['Borough'], inplace=True)
neighborhoods.loc[6]
        


Postcode                  M7A
Borough          Queen's Park
Neighbourhood    Queen's Park
Name: 6, dtype: object

Combine rows that have the same Postcode and Borough

In [9]:
neighborhoods=neighborhoods.groupby(['Postcode','Borough'])['Neighbourhood'].apply(', '.join).reset_index()
neighborhoods.head(12)

Postcode      Borough                                      Neighbourhood
0       M1B  Scarborough                                     Rouge, Malvern
1       M1C  Scarborough             Highland Creek, Rouge Hill, Port Union
2       M1E  Scarborough                  Guildwood, Morningside, West Hill
3       M1G  Scarborough                                             Woburn
4       M1H  Scarborough                                          Cedarbrae
5       M1J  Scarborough                                Scarborough Village
6       M1K  Scarborough        East Birchmount Park, Ionview, Kennedy Park
7       M1L  Scarborough                    Clairlea, Golden Mile, Oakridge
8       M1M  Scarborough    Cliffcrest, Cliffside, Scarborough Village West
9       M1N  Scarborough                        Birch Cliff, Cliffside West
10      M1P  Scarborough  Dorset Park, Scarborough Town Centre, Wexford ...
11      M1R  Scarborough                                  Maryvale, Wexford

Check the number of rows of the dataframe

In [10]:
neighborhoods.shape

(103, 3)

There are 103 rows in the dataframe

## Get the latitude and the longitude coordinates of each neighborhood

Read the csv file that has the geographical coordinates of each postal code and transform the data into a pandas dataframe

In [11]:
postcode = pd.read_csv('https://cocl.us/Geospatial_data')
postcode.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

Change the name of the column Postal Code to Postcode

In [12]:
postcode.rename(columns={'Postal Code':'Postcode'}, inplace=True) 
postcode.head()

Postcode   Latitude  Longitude
0      M1B  43.806686 -79.194353
1      M1C  43.784535 -79.160497
2      M1E  43.763573 -79.188711
3      M1G  43.770992 -79.216917
4      M1H  43.773136 -79.239476

Merge the two dataframes

In [13]:
neighborhoods = neighborhoods.merge(postcode, on='Postcode')
neighborhoods.head(12)

Postcode      Borough                                      Neighbourhood  \
0       M1B  Scarborough                                     Rouge, Malvern   
1       M1C  Scarborough             Highland Creek, Rouge Hill, Port Union   
2       M1E  Scarborough                  Guildwood, Morningside, West Hill   
3       M1G  Scarborough                                             Woburn   
4       M1H  Scarborough                                          Cedarbrae   
5       M1J  Scarborough                                Scarborough Village   
6       M1K  Scarborough        East Birchmount Park, Ionview, Kennedy Park   
7       M1L  Scarborough                    Clairlea, Golden Mile, Oakridge   
8       M1M  Scarborough    Cliffcrest, Cliffside, Scarborough Village West   
9       M1N  Scarborough                        Birch Cliff, Cliffside West   
10      M1P  Scarborough  Dorset Park, Scarborough Town Centre, Wexford ...   
11      M1R  Scarborough                                  Maryvale, Wexford   

     Latitude  Longitude  
0   43.806686 -79.194353  
1   43.784535 -79.160497  
2   43.763573 -79.188711  
3   43.770992 -79.216917  
4   43.773136 -79.239476  
5   43.744734 -79.239476  
6   43.727929 -79.262029  
7   43.711112 -79.284577  
8   43.716316 -79.239476  
9   43.692657 -79.264848  
10  43.757410 -79.273304  
11  43.750072 -79.295849

Use geopy library to get the latitude and longitude values of Toronto

In [14]:
address = 'Toronto, ON'

geolocator = Nominatim(user_agent="TO_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in meters).

In [15]:
!pip install shapely
import shapely.geometry

!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Toronto longitude={}, latitude={}'.format(longitude, latitude))
x, y = lonlat_to_xy(longitude, latitude)
print('Toronto UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Toronto longitude={}, latitude={}'.format(lo, la))

     |████████████████████████████████| 1.5MB 28.0MB/s eta 0:00:01
     |████████████████████████████████| 11.2MB 14.3MB/s eta 0:00:01
Coordinate transformation check
-------------------------------
Toronto longitude=-79.387207, latitude=43.653963
Toronto UTM X=-5310408.823314988, Y=10507908.004696788
Toronto longitude=-79.38720700000049, latitude=43.65396299999976


In [16]:
xs = []
ys = []

for n in neighborhoods.index:
    xs.append(lonlat_to_xy(neighborhoods['Longitude'][n],neighborhoods['Latitude'][n])[0])
    ys.append(lonlat_to_xy(neighborhoods['Longitude'][n],neighborhoods['Latitude'][n])[1])
    

neighborhoods = neighborhoods.assign(X = xs, Y = ys) 
neighborhoods.head()

Postcode      Borough                           Neighbourhood   Latitude  \
0      M1B  Scarborough                          Rouge, Malvern  43.806686   
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2      M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3      M1G  Scarborough                                  Woburn  43.770992   
4      M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude             X             Y  
0 -79.194353 -5.288536e+06  1.048305e+07  
1 -79.160497 -5.292465e+06  1.047953e+07  
2 -79.188711 -5.295454e+06  1.048313e+07  
3 -79.216917 -5.293931e+06  1.048625e+07  
4 -79.239476 -5.293314e+06  1.048881e+07

## Explore and cluster the neighborhoods in Toronto

### Create a map of Toronto with neighborhoods superimposed on top

Use geopy library to get the latitude and longitude values of Toronto

In [17]:
address = 'Toronto, ON'

geolocator = Nominatim(user_agent="TO_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


create map of Toronto using latitude and longitude values

In [18]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

## Foursquare

Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Italian restaurant' category, as we need info on Italian restaurants in the neighborhood.

Define Foursquare Credentials and Version

In [19]:
CLIENT_ID = 'PEZ3EJJNRHSCBBQFXIHPAJSCAHSES0RQQG513UK5UFPR5KCM' # your Foursquare ID
CLIENT_SECRET = 'HAH5GZURGXMPW2UBWV1GWDKKVJ1CYCTHHFSI3SHCRKE3FZ2J' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: PEZ3EJJNRHSCBBQFXIHPAJSCAHSES0RQQG513UK5UFPR5KCM
CLIENT_SECRET:HAH5GZURGXMPW2UBWV1GWDKKVJ1CYCTHHFSI3SHCRKE3FZ2J


In [20]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [21]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, CLIENT_ID, CLIENT_SECRET, radius=500, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_italian:
                    italian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, italian_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
italian_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('italian_restaurants_350.pkl', 'rb') as f:
        italian_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, italian_restaurants, location_restaurants = get_restaurants(neighborhoods['Latitude'], neighborhoods['Longitude'])
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('italian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(italian_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
        

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [22]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 651
Total number of Italian restaurants: 60
Percentage of Italian restaurants: 9.22%
Average number of restaurants in neighborhood: 3.4854368932038833


In [23]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('517dcdb6f1363b7a770a8424', "Meena's Fine Foods", 43.80447575837742, -79.19975280761719, '1295 Morningside Avenue, Unit 22 (Sheppard Avenue East), Scarborough ON M1B 4Z4, Canada', 498, False, -5288821.910135813, 10483711.705529414)
('57fd24f6cd1083addfd77bf9', 'Sail Sushi', 43.765951, -79.191275, '9-4352 Kingston Rd, Scarborough ON M1E 2M8, Canada', 335, False, -5295045.162719969, 10483382.37083262)
('5411f741498e9ebd5e35d8bd', 'Big Bite Burrito', 43.766299084470795, -79.19071980583941, '4383 Kingston rd., Scarborough ON, Canada', 343, False, -5294996.593606516, 10483312.590719065)
('4de0403ed4c040523ea079f4', 'Korean Grill House', 43.7708117291354, -79.21450208834013, '369 Yonge Street, Toronto ON, Canada', 195, False, -5293989.680591432, 10485975.362196662)
('52b128ae498ee935a36869a6', 'El rey del cabrito, monterrey city mexico', 43.7688, -79.2198, 'Ave. Gonzalitos, Monterrey Nuevo Leon. Mexico, Canada', 336, False, -5294244.549798208,

In [24]:
print('List of Italian restaurants')
print('---------------------------')
for r in list(italian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(italian_restaurants))

List of Italian restaurants
---------------------------
('4b5a2bf2f964a520deb128e3', 'Remezzo Italian Bistro', 43.778649, -79.308264, '3335 Sheppard Ave E (at Warden Ave.), Scarborough ON M1T 3K2, Canada', 460, True, -5291586.681061929, 10496634.128593037)
('4bdaff7463c5c9b67bcb2568', 'Sorento Restaurant', 43.72657509457231, -79.34198930569546, '900 Don Mills Rd., Toronto ON, Canada', 114, True, -5299436.539560529, 10501419.375027534)
('4e3dbb5e45dd68e3273e03b7', 'Cafe Fiorentina', 43.677743, -79.350115, '463 Danforth Ave (Logan Ave), Toronto ON M4K 1P1, Canada', 261, True, -5307097.990499288, 10503207.509265002)
('4af4e0d0f964a5202ff721e3', '7 Numbers', 43.677061774959824, -79.35393428891682, '307 Danforth Ave. (at Bowden St), Toronto ON, Canada', 311, True, -5307157.94152504, 10503660.32483632)
('4af6e7a0f964a520060422e3', 'Il Fornello', 43.67860392856738, -79.34690364849348, '576 Danforth Ave. (at Carlaw Ave.), Toronto ON M4K 1R1, Canada', 438, True, -5307001.716215332, 10502821.756

In [25]:
print('Restaurants around location')
print('---------------------------')
for i in range(0, 103):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 1: 
Restaurants around location 2: 
Restaurants around location 3: 
Restaurants around location 4: Korean Grill House
Restaurants around location 5: Federick Restaurant, Drupati's Roti & Doubles, Thai One On
Restaurants around location 6: 
Restaurants around location 7: 
Restaurants around location 8: taste of afghanistan
Restaurants around location 9: Vincent's Spot
Restaurants around location 10: UME Fashion Sushi
Restaurants around location 11: Karaikudi Chettinad South Indian Restaurant
Restaurants around location 12: 
Restaurants around location 13: Inchen House Korean Restaurant
Restaurants around location 14: 
Restaurants around location 15: 
Restaurants around location 16: Mr Congee Chinese Cuisine 龍粥記, Phoenix Restaurant 金鳳餐廳, Yamamoto Japanese Cuisine 山本盛世, Olives
Restaurants around location 17: 
Restaurants around location 18: Villa Madina
Restaurants around location 19: Moxie's Classic Grill

Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in red

In [26]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=13)
folium.Marker([latitude, longitude], popup='Toronto').add_to(map_toronto)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_toronto)
map_toronto

Looking good. So now we have all the restaurants in Toronto, and we know which ones are Italian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology

In this project we will direct our efforts on detecting areas of Toronto that have low restaurant density, particularly those with low number of Italian restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required data: location and type (category) of every restaurant within 6km from Downtown Toronto. We have also identified Italian restaurants (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of 'restaurant density' across different areas of Toronto - we will use heatmaps to identify a few promising areas close to center with low number of restaurants in general (and no Italian restaurants in vicinity) and focus our attention on those areas.

In third step we will get the 10 most common venues in each neighborhood and filter the neighborhoods that have preference for Italian Restaurant.

In final step we will focus on most promising areas and within those create clusters of locations that meet some basic requirements established in discussion with stakeholders: we will take into consideration locations with no more than two restaurants in radius of 250 meters, and we want locations without Italian restaurants in radius of 400 meters. We will present map of all such locations but also create clusters (using k-means clustering) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis

### Basic explanatory data analysis

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the number of restaurants in every area candidate:

In [27]:
location_restaurants_count = [len(res) for res in location_restaurants]

neighborhoods['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

neighborhoods.head(10)

Average number of restaurants in every area with radius=300m: 3.4854368932038833


Postcode      Borough                                    Neighbourhood  \
0      M1B  Scarborough                                   Rouge, Malvern   
1      M1C  Scarborough           Highland Creek, Rouge Hill, Port Union   
2      M1E  Scarborough                Guildwood, Morningside, West Hill   
3      M1G  Scarborough                                           Woburn   
4      M1H  Scarborough                                        Cedarbrae   
5      M1J  Scarborough                              Scarborough Village   
6      M1K  Scarborough      East Birchmount Park, Ionview, Kennedy Park   
7      M1L  Scarborough                  Clairlea, Golden Mile, Oakridge   
8      M1M  Scarborough  Cliffcrest, Cliffside, Scarborough Village West   
9      M1N  Scarborough                      Birch Cliff, Cliffside West   

    Latitude  Longitude             X             Y  Restaurants in area  
0  43.806686 -79.194353 -5.288536e+06  1.048305e+07                    0  
1  43.784535 -79.160497 -5.292465e+06  1.047953e+07                    0  
2  43.763573 -79.188711 -5.295454e+06  1.048313e+07                    0  
3  43.770992 -79.216917 -5.293931e+06  1.048625e+07                    1  
4  43.773136 -79.239476 -5.293314e+06  1.048881e+07                    3  
5  43.744734 -79.239476 -5.297828e+06  1.048929e+07                    0  
6  43.727929 -79.262029 -5.300221e+06  1.049218e+07                    0  
7  43.711112 -79.284577 -5.302614e+06  1.049507e+07                    1  
8  43.716316 -79.239476 -5.302346e+06  1.048978e+07                    1  
9  43.692657 -79.264848 -5.305795e+06  1.049311e+07                    1

OK, now let's calculate the distance to nearest Italian restaurant from neighborhood (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [28]:
distances_to_italian_restaurant = []

for area_x, area_y in zip(neighborhoods['X'], neighborhoods['Y']):
    min_distance = 100000
    for res in italian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_italian_restaurant.append(min_distance)

neighborhoods['Distance to Italian restaurant'] = distances_to_italian_restaurant
neighborhoods.head()

Postcode      Borough                           Neighbourhood   Latitude  \
0      M1B  Scarborough                          Rouge, Malvern  43.806686   
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2      M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3      M1G  Scarborough                                  Woburn  43.770992   
4      M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude             X             Y  Restaurants in area  \
0 -79.194353 -5.288536e+06  1.048305e+07                    0   
1 -79.160497 -5.292465e+06  1.047953e+07                    0   
2 -79.188711 -5.295454e+06  1.048313e+07                    0   
3 -79.216917 -5.293931e+06  1.048625e+07                    1   
4 -79.239476 -5.293314e+06  1.048881e+07                    3   

   Distance to Italian restaurant  
0                    13918.828519  
1                    17128.571805  
2                    14049.946922  
3                    10645.167670  
4                     8011.305819

In [29]:
print('Average distance to closest Italian restaurant from each area center:', neighborhoods['Distance to Italian restaurant'].mean())

Average distance to closest Italian restaurant from each area center: 4915.439144350742


OK, so **on average Italian restaurant can be found within ~5000m** from every Neighborhood. That's very far!

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show a few circles indicating distance of 1km, 2km and 3km from Toronto.

In [30]:
def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

In [31]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

In [32]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_toronto) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_toronto)
folium.Marker([latitude, longitude], popup='Toronto').add_to(map_toronto)
folium.Circle([latitude, longitude], radius=1000, fill=False, color='white').add_to(map_toronto)
folium.Circle([latitude, longitude], radius=2000, fill=False, color='white').add_to(map_toronto)
folium.Circle([latitude, longitude], radius=3000, fill=False, color='white').add_to(map_toronto)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  

map_toronto

Looks like a few restaurants can be found in the suburban areas. 


Let's create another heatmap map showing **heatmap/density of Italian restaurants** only.

In [33]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_toronto) #cartodbpositron cartodbdark_matter
HeatMap(italian_latlons).add_to(map_toronto)
folium.Marker([latitude, longitude], popup='Toronto').add_to(map_toronto)
folium.Circle([latitude, longitude], radius=1000, fill=False, color='white').add_to(map_toronto)
folium.Circle([latitude, longitude], radius=2000, fill=False, color='white').add_to(map_toronto)
folium.Circle([latitude, longitude], radius=3000, fill=False, color='white').add_to(map_toronto)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  

map_toronto

This map is not so 'hot' (Italian restaurants represent a subset of ~9.1% of all restaurants in Toronto) but it also indicates higher density of existing Italian restaurants directly in the south of Toronto, with closest pockets of low Italian restaurant density positioned east, west and North from city center.

### Find the neighborhoods that prefer Italian Restaurants

#### Explore the first neighborhood in our dataframe

Get the neighborhood's name

In [34]:
neighborhoods.loc[0,'Neighbourhood']

'Rouge, Malvern'

Get the neighborhood's latitude and longitude values.

In [35]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0, 'Neighbourhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Rouge, Malvern are 43.806686299999996, -79.19435340000001.


Now, let's get the top 100 venues that are in Rouge, Malvern within a radius of 1500 meters

First, let's create the GET request URL. Name your URL url.

In [36]:
LIMIT = 100 
radius = 1500

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

url

'https://api.foursquare.com/v2/venues/explore?&client_id=PEZ3EJJNRHSCBBQFXIHPAJSCAHSES0RQQG513UK5UFPR5KCM&client_secret=HAH5GZURGXMPW2UBWV1GWDKKVJ1CYCTHHFSI3SHCRKE3FZ2J&v=20180605&ll=43.806686299999996,-79.19435340000001&radius=1500&limit=100'

Send the GET request and examine the resutls

In [37]:
import requests
results = requests.get(url).json()

Borrow the get_category_type function from the Foursquare lab

In [38]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a pandas dataframe.

In [39]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name                     categories        lat        lng
0   Images Salon & Spa                            Spa  43.802283 -79.198565
1    Canadiana exhibit                    Zoo Exhibit  43.817962 -79.193374
2       Caribbean Wave           Caribbean Restaurant  43.798558 -79.195777
3  Staples Morningside  Paper / Office Supplies Store  43.800285 -79.196607
4             Harvey's           Fast Food Restaurant  43.800106 -79.198258

And how many venues were returned by Foursquare?

In [40]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

32 venues were returned by Foursquare.


#### Explore all Neighborhoods in Toronto

Let's create a function to repeat the same process to all the neighborhoods in Toronto

In [41]:
def getNearbyVenues(names, latitudes, longitudes, radius=1500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Now write the code to run the above function on each neighborhood and create a new dataframe called toronto_venues

In [42]:
toronto_venues = getNearbyVenues(names=neighborhoods['Neighbourhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Rouge, Malvern
Highland Creek, Rouge Hill, Port Union
Guildwood, Morningside, West Hill
Woburn
Cedarbrae
Scarborough Village
East Birchmount Park, Ionview, Kennedy Park
Clairlea, Golden Mile, Oakridge
Cliffcrest, Cliffside, Scarborough Village West
Birch Cliff, Cliffside West
Dorset Park, Scarborough Town Centre, Wexford Heights
Maryvale, Wexford
Agincourt
Clarks Corners, Sullivan, Tam O'Shanter
Agincourt North, L'Amoreaux East, Milliken, Steeles East
L'Amoreaux West
Upper Rouge
Hillcrest Village
Fairview, Henry Farm, Oriole
Bayview Village
Silver Hills, York Mills
Newtonbrook, Willowdale
Willowdale South
York Mills West
Willowdale West
Parkwoods
Don Mills North
Flemingdon Park, Don Mills South
Bathurst Manor, Downsview North, Wilson Heights
Northwood Park, York University
CFB Toronto, Downsview East
Downsview West
Downsview Central
Downsview Northwest
Victoria Village
Woodbine Gardens, Parkview Hill
Woodbine Heights
The Beaches
Leaside
Thorncliffe Park
East Toronto
The Danforth West, 

Let's check the size of the resulting dataframe

In [43]:
print(toronto_venues.shape)
toronto_venues.head()

(6815, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Rouge, Malvern              43.806686              -79.194353   
1  Rouge, Malvern              43.806686              -79.194353   
2  Rouge, Malvern              43.806686              -79.194353   
3  Rouge, Malvern              43.806686              -79.194353   
4  Rouge, Malvern              43.806686              -79.194353   

                 Venue  Venue Latitude  Venue Longitude  \
0   Images Salon & Spa       43.802283       -79.198565   
1    Canadiana exhibit       43.817962       -79.193374   
2       Caribbean Wave       43.798558       -79.195777   
3  Staples Morningside       43.800285       -79.196607   
4             Harvey's       43.800106       -79.198258   

                  Venue Category  
0                            Spa  
1                    Zoo Exhibit  
2           Caribbean Restaurant  
3  Paper / Office Supplies Store  
4           Fast Food Restaurant

Let's check how many venues were returned for each neighborhood

In [44]:
toronto_venues.groupby('Neighborhood').count().head()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide, King, Richmond                                              100   
Agincourt                                                              59   
Agincourt North, L'Amoreaux East, Milliken, Ste...                     69   
Albion Gardens, Beaumond Heights, Humbergate, J...                     27   
Alderwood, Long Branch                                                 43   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Adelaide, King, Richmond                                               100   
Agincourt                                                               59   
Agincourt North, L'Amoreaux East, Milliken, Ste...                      69   
Albion Gardens, Beaumond Heights, Humbergate, J...                      27   
Alderwood, Long Branch                                                  43   

                                                    Venue  Venue Latitude  \
Neighborhood                                                                
Adelaide, King, Richmond                              100             100   
Agincourt                                              59              59   
Agincourt North, L'Amoreaux East, Milliken, Ste...     69              69   
Albion Gardens, Beaumond Heights, Humbergate, J...     27              27   
Alderwood, Long Branch                                 43              43   

                                                    Venue Longitude  \
Neighborhood                                                          
Adelaide, King, Richmond                                        100   
Agincourt                                                        59   
Agincourt North, L'Amoreaux East, Milliken, Ste...               69   
Albion Gardens, Beaumond Heights, Humbergate, J...               27   
Alderwood, Long Branch                                           43   

                                                    Venue Category  
Neighborhood                                                        
Adelaide, King, Richmond                                       100  
Agincourt                                                       59  
Agincourt North, L'Amoreaux East, Milliken, Ste...              69  
Albion Gardens, Beaumond Heights, Humbergate, J...              27  
Alderwood, Long Branch                                          43

Let's find out how many unique categories can be curated from all the returned venues

In [45]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 343 uniques categories.


#### Analyze Each Neighborhood

one hot encoding

In [46]:
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Zoo Exhibit  Accessories Store  Afghan Restaurant  African Restaurant  \
0            0                  0                  0                   0   
1            1                  0                  0                   0   
2            0                  0                  0                   0   
3            0                  0                  0                   0   
4            0                  0                  0                   0   

   Airport  Airport Lounge  American Restaurant  Amphitheater  Animal Shelter  \
0        0               0                    0             0               0   
1        0               0                    0             0               0   
2        0               0                    0             0               0   
3        0               0                    0             0               0   
4        0               0                    0             0               0   

   Antique Shop  ...  Vietnamese Restaurant  Volleyball Court  \
0             0  ...                      0                 0   
1             0  ...                      0                 0   
2             0  ...                      0                 0   
3             0  ...                      0                 0   
4             0  ...                      0                 0   

   Warehouse Store  Whisky Bar  Wine Bar  Wine Shop  Wings Joint  \
0                0           0         0          0            0   
1                0           0         0          0            0   
2                0           0         0          0            0   
3                0           0         0          0            0   
4                0           0         0          0            0   

   Women's Store  Yoga Studio  Zoo  
0              0            0    0  
1              0            0    0  
2              0            0    0  
3              0            0    0  
4              0            0    0  

[5 rows x 343 columns]

And let's examine the new dataframe size.

In [47]:
toronto_onehot.shape

(6815, 343)

Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [48]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped.head()

Neighborhood  Zoo Exhibit  \
0                           Adelaide, King, Richmond          0.0   
1                                          Agincourt          0.0   
2  Agincourt North, L'Amoreaux East, Milliken, St...          0.0   
3  Albion Gardens, Beaumond Heights, Humbergate, ...          0.0   
4                             Alderwood, Long Branch          0.0   

   Accessories Store  Afghan Restaurant  African Restaurant  Airport  \
0                0.0                0.0                 0.0      0.0   
1                0.0                0.0                 0.0      0.0   
2                0.0                0.0                 0.0      0.0   
3                0.0                0.0                 0.0      0.0   
4                0.0                0.0                 0.0      0.0   

   Airport Lounge  American Restaurant  Amphitheater  Animal Shelter  ...  \
0             0.0                 0.02           0.0             0.0  ...   
1             0.0                 0.00           0.0             0.0  ...   
2             0.0                 0.00           0.0             0.0  ...   
3             0.0                 0.00           0.0             0.0  ...   
4             0.0                 0.00           0.0             0.0  ...   

   Vietnamese Restaurant  Volleyball Court  Warehouse Store  Whisky Bar  \
0               0.000000               0.0              0.0         0.0   
1               0.016949               0.0              0.0         0.0   
2               0.028986               0.0              0.0         0.0   
3               0.000000               0.0              0.0         0.0   
4               0.000000               0.0              0.0         0.0   

   Wine Bar  Wine Shop  Wings Joint  Women's Store  Yoga Studio  Zoo  
0       0.0        0.0     0.000000            0.0         0.01  0.0  
1       0.0        0.0     0.000000            0.0         0.00  0.0  
2       0.0        0.0     0.000000            0.0         0.00  0.0  
3       0.0        0.0     0.000000            0.0         0.00  0.0  
4       0.0        0.0     0.023256            0.0         0.00  0.0  

[5 rows x 343 columns]

Let's confirm the new size

In [49]:
toronto_grouped.shape

(103, 343)

Let's print each neighborhood along with the top 5 most common venues

Let's put that into a pandas dataframe

First, let's write a function to sort the venues in descending order

In [50]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood

In [51]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                           Adelaide, King, Richmond           Coffee Shop   
1                                          Agincourt    Chinese Restaurant   
2  Agincourt North, L'Amoreaux East, Milliken, St...    Chinese Restaurant   
3  Albion Gardens, Beaumond Heights, Humbergate, ...           Coffee Shop   
4                             Alderwood, Long Branch                  Park   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                 Hotel                  Café               Theater   
1      Asian Restaurant         Shopping Mall        Breakfast Spot   
2              Pharmacy           Coffee Shop             BBQ Joint   
3  Fast Food Restaurant         Grocery Store           Pizza Place   
4     Convenience Store                  Café        Discount Store   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0             Gastropub           Pizza Place            Restaurant   
1           Supermarket  Caribbean Restaurant           Coffee Shop   
2           Pizza Place     Korean Restaurant       Bubble Tea Shop   
3           Flea Market   Fried Chicken Joint        Sandwich Place   
4      Toy / Game Store          Burger Joint            Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0      Sushi Restaurant    Italian Restaurant    Japanese Restaurant  
1  Cantonese Restaurant  Gym / Fitness Center                 Bakery  
2          Noodle House                Bakery           Dessert Shop  
3      Greek Restaurant     Electronics Store             Beer Store  
4           Coffee Shop         Grocery Store               Pharmacy

In [52]:
toronto_merged = neighborhoods

In [53]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighbourhood')
toronto_merged.head() # check the last columns!

Postcode      Borough                           Neighbourhood   Latitude  \
0      M1B  Scarborough                          Rouge, Malvern  43.806686   
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2      M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3      M1G  Scarborough                                  Woburn  43.770992   
4      M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude             X             Y  Restaurants in area  \
0 -79.194353 -5.288536e+06  1.048305e+07                    0   
1 -79.160497 -5.292465e+06  1.047953e+07                    0   
2 -79.188711 -5.295454e+06  1.048313e+07                    0   
3 -79.216917 -5.293931e+06  1.048625e+07                    1   
4 -79.239476 -5.293314e+06  1.048881e+07                    3   

   Distance to Italian restaurant 1st Most Common Venue 2nd Most Common Venue  \
0                    13918.828519           Zoo Exhibit  Fast Food Restaurant   
1                    17128.571805                   Gym    Italian Restaurant   
2                    14049.946922           Pizza Place  Fast Food Restaurant   
3                    10645.167670           Coffee Shop           Pizza Place   
4                     8011.305819           Coffee Shop        Clothing Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Pizza Place   Arts & Crafts Store           Coffee Shop   
1          Burger Joint                  Park         Grocery Store   
2        Breakfast Spot           Coffee Shop            Sports Bar   
3              Pharmacy     Indian Restaurant        Sandwich Place   
4     Indian Restaurant        Sandwich Place              Pharmacy   

           6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0  Paper / Office Supplies Store    Chinese Restaurant  Caribbean Restaurant   
1           Gym / Fitness Center        Breakfast Spot                 Hotel   
2                      Juice Bar                  Bank            Laundromat   
3           Fast Food Restaurant        Clothing Store                  Bank   
4                    Wings Joint         Women's Store                 Hotel   

  9th Most Common Venue 10th Most Common Venue  
0        Sandwich Place          Movie Theater  
1          Cupcake Shop              Drugstore  
2           Supermarket       Storage Facility  
3           Supermarket     Chinese Restaurant  
4    Light Rail Station    Sporting Goods Shop

In [54]:
toronto_merged.iloc[49]

Postcode                                                                        M4V
Borough                                                             Central Toronto
Neighbourhood                     Deer Park, Forest Hill SE, Rathnelly, South Hi...
Latitude                                                                    43.6864
Longitude                                                                     -79.4
X                                                                      -5.30508e+06
Y                                                                       1.05088e+07
Restaurants in area                                                               0
Distance to Italian restaurant                                               3084.5
1st Most Common Venue                                            Italian Restaurant
2nd Most Common Venue                                                   Coffee Shop
3rd Most Common Venue                                                       

In [55]:
results = []

df1 = toronto_merged

for n in toronto_merged.index:
    results.append('Italian Restaurant' in df1.iloc[n, 9:].values)
    
toronto_merged = toronto_merged.assign(Result = results)
toronto_merged.head()

Postcode      Borough                           Neighbourhood   Latitude  \
0      M1B  Scarborough                          Rouge, Malvern  43.806686   
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2      M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3      M1G  Scarborough                                  Woburn  43.770992   
4      M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude             X             Y  Restaurants in area  \
0 -79.194353 -5.288536e+06  1.048305e+07                    0   
1 -79.160497 -5.292465e+06  1.047953e+07                    0   
2 -79.188711 -5.295454e+06  1.048313e+07                    0   
3 -79.216917 -5.293931e+06  1.048625e+07                    1   
4 -79.239476 -5.293314e+06  1.048881e+07                    3   

   Distance to Italian restaurant 1st Most Common Venue 2nd Most Common Venue  \
0                    13918.828519           Zoo Exhibit  Fast Food Restaurant   
1                    17128.571805                   Gym    Italian Restaurant   
2                    14049.946922           Pizza Place  Fast Food Restaurant   
3                    10645.167670           Coffee Shop           Pizza Place   
4                     8011.305819           Coffee Shop        Clothing Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Pizza Place   Arts & Crafts Store           Coffee Shop   
1          Burger Joint                  Park         Grocery Store   
2        Breakfast Spot           Coffee Shop            Sports Bar   
3              Pharmacy     Indian Restaurant        Sandwich Place   
4     Indian Restaurant        Sandwich Place              Pharmacy   

           6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0  Paper / Office Supplies Store    Chinese Restaurant  Caribbean Restaurant   
1           Gym / Fitness Center        Breakfast Spot                 Hotel   
2                      Juice Bar                  Bank            Laundromat   
3           Fast Food Restaurant        Clothing Store                  Bank   
4                    Wings Joint         Women's Store                 Hotel   

  9th Most Common Venue 10th Most Common Venue  Result  
0        Sandwich Place          Movie Theater   False  
1          Cupcake Shop              Drugstore    True  
2           Supermarket       Storage Facility   False  
3           Supermarket     Chinese Restaurant   False  
4    Light Rail Station    Sporting Goods Shop   False

In [56]:
toronto_merged_italian = toronto_merged.loc[(toronto_merged['Restaurants in area'] < 2) & (toronto_merged['Distance to Italian restaurant'] > 3000) & toronto_merged['Result'] == True]
toronto_merged_italian

Postcode          Borough  \
1       M1C      Scarborough   
20      M2L       North York   
26      M3B       North York   
49      M4V  Central Toronto   
73      M6C             York   
74      M6E             York   
92      M8Z        Etobicoke   
96      M9L       North York   
97      M9M       North York   

                                        Neighbourhood   Latitude  Longitude  \
1              Highland Creek, Rouge Hill, Port Union  43.784535 -79.160497   
20                           Silver Hills, York Mills  43.757490 -79.374714   
26                                    Don Mills North  43.745906 -79.352188   
49  Deer Park, Forest Hill SE, Rathnelly, South Hi...  43.686412 -79.400049   
73                                 Humewood-Cedarvale  43.693781 -79.428191   
74                                Caledonia-Fairbanks  43.689026 -79.453512   
92  Kingsway Park South West, Mimico NW, The Queen...  43.628841 -79.520999   
96                                      Humber Summit  43.756303 -79.565963   
97                                   Emery, Humberlea  43.724766 -79.532242   

               X             Y  Restaurants in area  \
1  -5.292465e+06  1.047953e+07                    0   
20 -5.294111e+06  1.050465e+07                    0   
26 -5.296236e+06  1.050226e+07                    0   
49 -5.305083e+06  1.050882e+07                    0   
73 -5.303550e+06  1.051193e+07                    0   
74 -5.303979e+06  1.051494e+07                    0   
92 -5.312667e+06  1.052382e+07                    0   
96 -5.291821e+06  1.052668e+07                    0   
97 -5.297272e+06  1.052337e+07                    0   

    Distance to Italian restaurant 1st Most Common Venue  \
1                     17128.571805                   Gym   
20                     6228.680391           Coffee Shop   
26                     3308.440237           Coffee Shop   
49                     3084.504403    Italian Restaurant   
73                     3703.697054           Coffee Shop   
74                     4047.503205    Italian Restaurant   
92                     5084.670599           Coffee Shop   
96                    17217.037638                  Park   
97                    12256.070881           Golf Course   

   2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
1     Italian Restaurant          Burger Joint                    Park   
20                  Bank                  Park             Supermarket   
26   Japanese Restaurant           Pizza Place              Restaurant   
49           Coffee Shop                  Café                    Park   
73           Pizza Place    Italian Restaurant                    Café   
74           Coffee Shop           Pizza Place  Furniture / Home Store   
92            Restaurant  Fast Food Restaurant        Sushi Restaurant   
96     Electronics Store      Asian Restaurant      Italian Restaurant   
97           Coffee Shop    Italian Restaurant            Liquor Store   

   5th Most Common Venue 6th Most Common Venue   7th Most Common Venue  \
1          Grocery Store  Gym / Fitness Center          Breakfast Spot   
20    Italian Restaurant          Burger Joint  Furniture / Home Store   
26        Sandwich Place          Burger Joint      Italian Restaurant   
49      Sushi Restaurant   American Restaurant             Pizza Place   
73                  Bank                Bakery          Sandwich Place   
74                Bakery              Pharmacy    Caribbean Restaurant   
92                  Bank                Bakery      Italian Restaurant   
96          Skating Rink                  Bank                  Bakery   
97        Sandwich Place         Grocery Store       Electronics Store   

            8th Most Common Venue 9th Most Common Venue  \
1                           Hotel          Cupcake Shop   
20                       Pharmacy        Sandwich Place   
26                           Bank                  Park   
49  Vegetarian / Vega

Based on the heatmap and the table, we will now focus our analysis on Neighbourhoods Deer Park, Forest Hill SE, Rathnelly and South Hill. There is no restaurant in these areas and the cloest Italian restaurant is 3084 meters away. However, residents in these neighborhoods like Italian Restaurant, so we think these aress might be ideal for a new Italian restaurant.

## Targeted Neighborhoods: Deer Park, Forest Hill SE, Rathnelly and South Hill

Deer Park, Forest Hill SE, Rathnelly and South Hill are in the heart of Toronto. Analysis of popular travel guides and web sites often mention Deer Park as beautifull, interesting and Commercial. 

"sandwiched between Forest Hill on its western flank and Moore Park to the east, Deer Park is utterly unlike either of them—it's more commercial, a fast-changing community dominated by apartment dwellers." (Robert Fulford)

Let's define new, more narrow region of interest, which will include low-restaurant-count parts of Deer Park, Forest Hill SE and Rathnelly closest to Downtown Toronto.

In [57]:
dp_center_lat = toronto_merged.iloc[49][3]
dp_center_lon = toronto_merged.iloc[49][4]
dp_center = [dp_center_lat , dp_center_lon]

In [58]:
map_toronto = folium.Map(location=dp_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_toronto)
folium.Marker(dp_center).add_to(map_toronto)
folium.Circle(dp_center, radius=2000, color='white', fill=True, fill_opacity=0.4).add_to(map_toronto)
map_toronto

Great! This nicely covers most the pockets of low restaurant density in Deer Park, Forest Hill SE, Rathnelly and South Hill

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [59]:
dp_center_x, dp_center_y = lonlat_to_xy(dp_center_lon, dp_center_lat)

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
dp_y_min = dp_center_y - 2500
dp_x_min = dp_center_x - 2500

dp_latitudes = []
dp_longitudes = []
dp_xs = []
dp_ys = []
for i in range(0, int(51/k)):
    y = dp_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = dp_x_min + j * x_step + x_offset
        d = calc_xy_distance(dp_center_x, dp_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            dp_latitudes.append(lat)
            dp_longitudes.append(lon)
            dp_xs.append(x)
            dp_ys.append(y)

print(len(dp_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: number of restaurants in vicinity (we'll use radius of 250 meters) and distance to closest Italian restaurant.

In [60]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

dp_restaurant_counts = []
dp_italian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(dp_xs, dp_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    dp_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, italian_restaurants)
    dp_italian_distances.append(distance)
print('done.')

Generating data on location candidates... done.


In [61]:
#Let's put this into dataframe
df_dp_locations = pd.DataFrame({'Latitude':dp_latitudes,
                                 'Longitude':dp_longitudes,
                                 'X':dp_xs,
                                 'Y':dp_ys,
                                 'Restaurants nearby':dp_restaurant_counts,
                                 'Distance to Italian restaurant':dp_italian_distances})

df_dp_locations.head(10)

Latitude  Longitude             X             Y  Restaurants nearby  \
0  43.687821 -79.378598 -5.305133e+06  1.050632e+07                   0   
1  43.688442 -79.378693 -5.305033e+06  1.050632e+07                   0   
2  43.684345 -79.378820 -5.305683e+06  1.050641e+07                   0   
3  43.684966 -79.378914 -5.305583e+06  1.050641e+07                   0   
4  43.685587 -79.379009 -5.305483e+06  1.050641e+07                   0   
5  43.686209 -79.379103 -5.305383e+06  1.050641e+07                   0   
6  43.686830 -79.379198 -5.305283e+06  1.050641e+07                   0   
7  43.687451 -79.379293 -5.305183e+06  1.050641e+07                   0   
8  43.688072 -79.379387 -5.305083e+06  1.050641e+07                   0   
9  43.688694 -79.379482 -5.304983e+06  1.050641e+07                   0   

   Distance to Italian restaurant  
0                     2748.135518  
1                     2652.690304  
2                     2934.218868  
3                     3027.540547  
4                     3062.990498  
5                     2965.877241  
6                     2868.962326  
7                     2772.266554  
8                     2675.813684  
9                     2579.630960

OK. Let us now filter those locations: we're interested only in locations with no more than two restaurants in radius of 250 meters, and no Italian restaurants in radius of 400 meters.

In [62]:
good_res_count = np.array((df_dp_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_dp_locations['Distance to Italian restaurant']>=400)
print('Locations with no Italian restaurants within 400m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_dp_locations[good_locations]

Locations with no more than two restaurants nearby: 2221
Locations with no Italian restaurants within 400m: 2261
Locations with both conditions met: 2221


Let's see how this looks on a map.

In [63]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_toronto = folium.Map(location=dp_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_toronto)
HeatMap(restaurant_latlons).add_to(map_toronto)
folium.Circle(dp_center, radius=2000, color='white', fill=True, fill_opacity=0.6).add_to(map_toronto)
folium.Marker(dp_center).add_to(map_toronto)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_toronto) 

map_toronto

Looking good. We now have a bunch of locations fairly close to Deer Park , and we know that each of those locations has no more than two restaurants in radius of 250m, and no Italian restaurant closer than 400m. Any of those locations is a potential candidate for a new Italian restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [64]:
map_toronto = folium.Map(location=dp_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_toronto)
folium.Marker(dp_center).add_to(map_toronto)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_toronto)
map_toronto

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and no Italian restaurants at all nearby.

Let us now cluster those locations to create centers of zones containing good locations. Those zones, their centers and addresses will be the final result of our analysis.

In [65]:
number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_toronto = folium.Map(location=dp_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_toronto)
HeatMap(restaurant_latlons).add_to(map_toronto)
folium.Circle(dp_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_toronto)
folium.Marker(dp_center).add_to(map_toronto)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_toronto) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_toronto)
map_toronto

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [66]:
map_toronto = folium.Map(location=dp_center, zoom_start=14)

folium.Circle(dp_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_toronto)
folium.Marker(dp_center).add_to(map_toronto)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_toronto) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_toronto)
map_toronto

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [67]:
from geopy.geocoders import Nominatim

candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')

geolocator = Nominatim(user_agent="a")
for lon, lat in cluster_centers:
    latlon = str(lat) +', '+ str(lon)
    addr = geolocator.reverse(latlon).address.replace(', Canada', '').replace(', Toronto, Ontario', '').replace(', Old Toronto', '')
    candidate_area_addresses.append(addr)
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, dp_center_x, dp_center_y)
    print('{}{} ====> {:.1f}km from Deer Park, Forest Hill SE, Rathnelly and South Hill'.format(addr, ' '*(50-len(addr)), d/1000))



Addresses of centers of areas recommended for further analysis

30, Hillsboro Avenue, Yorkville, University—Rosedale, M5R 1J3 ====> 1.9km from Deer Park, Forest Hill SE, Rathnelly and South Hill
438, Russell Hill Road, Forest Hill, Toronto—St. Paul's, M5P 2T6 ====> 1.9km from Deer Park, Forest Hill SE, Rathnelly and South Hill
134, Inglewood Drive, Moore Park, University—Rosedale, M4T 2B4 ====> 1.9km from Deer Park, Forest Hill SE, Rathnelly and South Hill
97, Wells Hill Avenue, St. Clair West, Toronto—St. Paul's, M6H 3L9 ====> 1.9km from Deer Park, Forest Hill SE, Rathnelly and South Hill
16, Oriole Gardens, Deer Park, Toronto—St. Paul's, M4V 2K5 ====> 0.9km from Deer Park, Forest Hill SE, Rathnelly and South Hill
30, Woodlawn Avenue West, University—Rosedale, M4T 1W5 ====> 0.8km from Deer Park, Forest Hill SE, Rathnelly and South Hill
584, Davenport Road, Tarragon Village, Toronto—St. Paul's, M5R 1K9 ====> 2.0km from Deer Park, Forest Hill SE, Rathnelly and South Hill
7, Thornwood Ro

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (all less than 2km from Deer Park, Forest Hill SE, Rathnelly and South Hill). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. All of the zones are located in Deer Park, Forest Hill SE, Rathnelly and South Hill, which we have identified as interesting due to being popular with residents, fairly close to Downtown Toronto and well connected by public transport.

In [68]:
map_toronto = folium.Map(location=dp_center, zoom_start=14)
folium.Circle(dp_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_toronto)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]]).add_to(map_toronto) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=200, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_toronto)
map_toronto

## Results and Discussion

Our analysis shows that although there are 655 restaurants in Toronto, there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected south from Toronto, so we focused our attention to areas north, east and west, corresponding to neighborhoods Deer Park, Forest Hill SE, Rathnelly and South Hill, which offer a combination of preference for Italian restaurant among residents, closeness to city center, strong socio-economic dynamics and a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest, we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Italian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Downtown Toronto but not crowded with existing restaurants (particularly Italian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion

Purpose of this project was to identify areas close to Downtown Toronto with low number of restaurants (particularly Italian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Italian restaurant. By calculating restaurant density distribution and filtering neighborhoods based on venues preferences from Foursquare data we have first identified several neighborhoods that justify further analysis (Deer Park, Forest Hill SE, Rathnelly and South Hill), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.